In [1]:
import pandas as pd
import os
import s3fs
import warnings
from datetime import date, timedelta, datetime
import numpy as np

In [7]:
# Import KPI construction functions
#exec(open('0_KPI_functions.py').read())
exec(open('../0_KPI_functions.py').read())


In [8]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

BUCKET = "projet-bdc2324-team1/0_Input/Company_10"
fs.ls(BUCKET)

['projet-bdc2324-team1/0_Input/Company_10/campaigns_information.csv',
 'projet-bdc2324-team1/0_Input/Company_10/customerplus_cleaned.csv',
 'projet-bdc2324-team1/0_Input/Company_10/products_purchased_reduced.csv',
 'projet-bdc2324-team1/0_Input/Company_10/target_information.csv']

In [10]:
BUCKET = "projet-bdc2324-team1"
FILE_KEY_S3 = "0_Input/Company_10/customerplus_cleaned.csv"
FILE_PATH_S3 = BUCKET + "/" + FILE_KEY_S3

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    df_customerplus_cleaned = pd.read_csv(file_in, sep=",")
 


In [11]:
BUCKET = "projet-bdc2324-team1"
FILE_KEY_S3 = "0_Input/Company_10/products_purchased_reduced.csv"
FILE_PATH_S3 = BUCKET + "/" + FILE_KEY_S3

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    purchases = pd.read_csv(file_in, sep=",", parse_dates = ['purchase_date'], date_parser=custom_date_parser)
 


/tmp/ipykernel_491/3710670046.py:6: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  purchases = pd.read_csv(file_in, sep=",", parse_dates = ['purchase_date'], date_parser=custom_date_parser)


In [12]:

dic_base=['campaigns_information','customerplus_cleaned','products_purchased_reduced','target_information']
for nom_base in dic_base:
    FILE_PATH_S3_fanta = 'projet-bdc2324-team1/0_Input/Company_10/' + nom_base + '.csv'
    with fs.open(FILE_PATH_S3_fanta, mode="rb") as file_in:
        globals()[nom_base] = pd.read_csv(file_in, sep=",")

In [13]:
target_information

id  customer_id           target_name  target_type_is_import  \
0      1165098       618562  Newsletter mensuelle                  False   
1      1165100       618559  Newsletter mensuelle                  False   
2      1165101       618561  Newsletter mensuelle                  False   
3      1165102       618560  Newsletter mensuelle                  False   
4      1165103       618558  Newsletter mensuelle                  False   
...        ...          ...                   ...                    ...   
69253  1698158        18580  Newsletter mensuelle                  False   
69254  1698159        18569  Newsletter mensuelle                  False   
69255  1698160         2962  Newsletter mensuelle                  False   
69256  1698161         3825  Newsletter mensuelle                  False   
69257  1698162         5731  Newsletter mensuelle                  False   

           target_type_name  
0      manual_static_filter  
1      manual_static_filter  
2      manual_static_filter  
3      manual_static_filter  
4      manual_static_filter  
...                     ...  
69253  manual_static_filter  
69254  manual_static_filter  
69255  manual_static_filter  
69256  manual_static_filter  
69257  manual_static_filter  

[69258 rows x 5 columns]

In [46]:
campaigns_kpi_function(campaigns)

<string>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


customer_id  nb_campaigns  nb_campaigns_opened    time_to_open
0               29             4                  NaN             NaT
1               37             3                  NaN             NaT
2               39             4                  1.0 0 days 05:16:38
3               41             4                  1.0 0 days 01:12:29
4               44             4                  NaN             NaT
...            ...           ...                  ...             ...
57138       827940             1                  NaN             NaT
57139       827941             1                  NaN             NaT
57140       827942             1                  NaN             NaT
57141       827943             1                  NaN             NaT
57142       827944             1                  NaN             NaT

[57143 rows x 4 columns]

In [52]:
# KPI sur le comportement d'achat
df_tickets_kpi = tickets_kpi_function(purchases)

In [73]:
df_tickets_kpi.isna().sum()

customer_id              0
nb_tickets               0
nb_purchases             0
total_amount             0
nb_suppliers             0
vente_internet_max       0
purchase_date_min        0
purchase_date_max        0
time_between_purchase    0
nb_tickets_internet      0
dtype: int64

In [76]:
 # KPI sur le comportement d'achat
    
df_tickets_kpi = tickets_kpi_function(tickets_information = purchases)

In [77]:
df_tickets_kpi

customer_id  nb_tickets  nb_purchases  total_amount  nb_suppliers  \
0            19482          88            29         872.0             2   
1            19484           3             2          62.0             1   
2            19485         131            21        1878.0             2   
3            19486          10             4          96.0             1   
4            19487           2             1          33.0             1   
...            ...         ...           ...           ...           ...   
26100       824877           1             1         -12.0             1   
26101       824878           1             1          12.0             1   
26102       824879           2             1         -38.0             1   
26103       824991          14             3        -100.0             1   
26104       824998           1             1          25.0             1   

       vente_internet_max  purchase_date_min  purchase_date_max  \
0                       1        2643.092500         718.149398   
1                       0        1745.021736        1743.045035   
2                       1        2649.044745          85.240845   
3                       0        1944.077604        1742.794225   
4                       0        1742.877766        1742.877766   
...                   ...                ...                ...   
26100                   0           5.956111           5.956111   
26101                   0           5.956921           5.956921   
26102                   0           5.226238           5.226238   
26103                   0           3.021539           3.017222   
26104                   0           0.072720           0.072720   

       time_between_purchase  nb_tickets_internet  
0                1924.943102                  8.0  
1                   1.976701                  0.0  
2                2563.803900                 84.0  
3                 201.283380                  0.0  
4                   0.000000                  0.0  
...                      ...                  ...  
26100               0.000000                  0.0  
26101               0.000000                  0.0  
26102               0.000000                  0.0  
26103               0.004317                  0.0  
26104               0.000000                  0.0  

[26105 rows x 10 columns]

In [57]:
 # KPI sur les données socio-démographiques
df_customerplus_clean = customerplus_kpi_function(df_customerplus_cleaned)
 
df_customerplus_clean

customer_id  street_id  structure_id  mcp_contact_id  fidelity  \
0           821538        139           NaN             NaN         0   
1           809126       1063           NaN             NaN         0   
2            11005       1063           NaN             NaN         0   
3            17663      12731           NaN             NaN         0   
4            38100      12395           NaN             NaN         0   
...            ...        ...           ...             ...       ...   
98789       766266        139           NaN        181304.0         0   
98790       766336        139           NaN        178189.0         0   
98791       766348        139           NaN        178141.0         0   
98792       766363        139           NaN        176807.0         0   
98793       766366        139           NaN        176788.0         0   

       tenant_id  is_partner  deleted_at  gender  is_email_true  ...  \
0            875       False         NaN       2           True  ...   
1            875       False         NaN       2           True  ...   
2            875       False         NaN       2          False  ...   
3            875       False         NaN       0          False  ...   
4            875       False         NaN       0           True  ...   
...          ...         ...         ...     ...            ...  ...   
98789        875       False         NaN       2           True  ...   
98790        875       False         NaN       2           True  ...   
98791        875       False         NaN       2           True  ...   
98792        875       False         NaN       2           True  ...   
98793        875       False         NaN       2           True  ...   

       total_price purchase_count  first_buying_date  country  gender_label  \
0              0.0              0                NaN      NaN         other   
1              0.0              0                NaN       fr         other   
2              NaN             14                NaN       fr         other   
3              NaN              1                NaN       fr        female   
4              NaN              1                NaN       fr        female   
...            ...            ...                ...      ...           ...   
98789          0.0              0                NaN      NaN         other   
98790          0.0              0                NaN      NaN         other   
98791          0.0              0                NaN      NaN         other   
98792          0.0              0                NaN      NaN         other   
98793          0.0              0                NaN      NaN         other   

       gender_female  gender_male  gender_other  country_fr  has_tags  
0                  0            0             1         NaN         0  
1                  0            0             1         1.0         0  
2                  0            0             1         1.0         0  
3                  1            0             0         1.0         0  
4                  1            0             0         1.0         0  
...              ...          ...           ...         ...       ...  
98789              0            0             1         NaN         0  
98790              0            0             1         NaN         0  
98791              0            0             1         NaN         0  
98792              0            0             1         NaN         0  
98793              0            0             1         NaN         0  

[98794 rows x 28 columns]

In [72]:
df_customerplus_clean.isna().sum()

customer_id                   0
street_id                     0
structure_id              96706
mcp_contact_id            19094
fidelity                      0
tenant_id                     0
is_partner                    0
deleted_at                98794
gender                        0
is_email_true                 0
opt_in                        0
last_buying_date          73081
max_price                 73081
ticket_sum                    0
average_price             35539
average_purchase_delay    73081
average_price_basket      73081
average_ticket_basket     73081
total_price               37542
purchase_count                0
first_buying_date         73081
country                   44192
gender_label                  0
gender_female                 0
gender_male                   0
gender_other                  0
country_fr                44192
has_tags                      0
dtype: int64

In [29]:
BUCKET = "projet-bdc2324-team1"
FILE_KEY_S3 = "0_Input/Company_10/campaigns_information.csv"
FILE_PATH_S3 = BUCKET + "/" + FILE_KEY_S3

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    campaigns = pd.read_csv(file_in, sep=",", parse_dates = ["opened_at", "sent_at", "delivered_at"], date_parser=custom_date_parser)
 


/tmp/ipykernel_438/1359829443.py:6: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  campaigns = pd.read_csv(file_in, sep=",", parse_dates = ["opened_at", "sent_at", "delivered_at"], date_parser=custom_date_parser)


In [32]:
BUCKET = "projet-bdc2324-team1"
FILE_KEY_S3 = "0_Input/Company_10/target_information.csv"
FILE_PATH_S3 = BUCKET + "/" + FILE_KEY_S3

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    targets = pd.read_csv(file_in, sep=",")
 


In [65]:
targets

id  customer_id           target_name  target_type_is_import  \
0      1165098       618562  Newsletter mensuelle                  False   
1      1165100       618559  Newsletter mensuelle                  False   
2      1165101       618561  Newsletter mensuelle                  False   
3      1165102       618560  Newsletter mensuelle                  False   
4      1165103       618558  Newsletter mensuelle                  False   
...        ...          ...                   ...                    ...   
69253  1698158        18580  Newsletter mensuelle                  False   
69254  1698159        18569  Newsletter mensuelle                  False   
69255  1698160         2962  Newsletter mensuelle                  False   
69256  1698161         3825  Newsletter mensuelle                  False   
69257  1698162         5731  Newsletter mensuelle                  False   

           target_type_name  
0      manual_static_filter  
1      manual_static_filter  
2      manual_static_filter  
3      manual_static_filter  
4      manual_static_filter  
...                     ...  
69253  manual_static_filter  
69254  manual_static_filter  
69255  manual_static_filter  
69256  manual_static_filter  
69257  manual_static_filter  

[69258 rows x 5 columns]

In [64]:
pd.reset_option('display.max_rows',70000)


In [68]:
targets["target_name"].head(10000)

0       Newsletter mensuelle
1       Newsletter mensuelle
2       Newsletter mensuelle
3       Newsletter mensuelle
4       Newsletter mensuelle
                ...         
9995    Newsletter mensuelle
9996    Newsletter mensuelle
9997    Newsletter mensuelle
9998    Newsletter mensuelle
9999    Newsletter mensuelle
Name: target_name, Length: 10000, dtype: object

In [88]:
companies = {'musee' : ['1', '2', '3', '4', '101'],
            'sport': ['5', '6', '7', '8', '9'],
            'musique' : ['10', '11', '12', '13', '14']}

In [90]:
type_of_comp = input('Choisissez le type de compagnie : sport ? musique ? musee ?')
list_of_comp = companies[type_of_comp] 


Choisissez le type de compagnie : sport ? musique ? musee ? musique


In [91]:
# Dossier d'exportation
BUCKET_OUT = f'projet-bdc2324-team1/Generalization/{type_of_comp}'

In [100]:
BUCKET_OUT

'projet-bdc2324-team1/Generalization/musique'

In [96]:
'projet-bdc2324-team1/Generalization/musique'

'projet-bdc2324-team1/Generalization/musique'

In [98]:
def display_covering_time(df, company, datecover):
    """
    This function draws the time coverage of each company
    """
    min_date = df['purchase_date'].min().strftime("%Y-%m-%d")
    max_date = df['purchase_date'].max().strftime("%Y-%m-%d")
    datecover[company] = [datetime.strptime(min_date, "%Y-%m-%d") + timedelta(days=x) for x in range((datetime.strptime(max_date, "%Y-%m-%d") - datetime.strptime(min_date, "%Y-%m-%d")).days)]
    print(f'Couverture Company {company} : {min_date} - {max_date}')
    return datecover


def compute_time_intersection(datecover):
    """
    This function returns the time coverage for all companies
    """
    timestamps_sets = [set(timestamps) for timestamps in datecover.values()]
    intersection = set.intersection(*timestamps_sets)
    intersection_list = list(intersection)
    formated_dates = [dt.strftime("%Y-%m-%d") for dt in intersection_list]
    return sorted(formated_dates)


def df_coverage_modelization(sport, coverage_train = 0.7):
    """
    This function returns start_date, end_of_features and final dates
    that help to construct train and test datasets
    """
    datecover = {}
    for company in sport:
        df_products_purchased_reduced = display_databases(company, file_name = "products_purchased_reduced",
                                                          datetime_col = ['purchase_date'])
        datecover = display_covering_time(df_products_purchased_reduced, company, datecover)
    #print(datecover.keys())
    dt_coverage = compute_time_intersection(datecover)
    start_date = dt_coverage[0]
    end_of_features = dt_coverage[int(0.7 * len(dt_coverage))]
    final_date = dt_coverage[-1]
    return start_date, end_of_features, final_date
    

def dataset_construction(min_date, end_features_date, max_date, directory_path):
    
    # Import customerplus
    df_customerplus_clean_0 = display_databases(directory_path, file_name = "customerplus_cleaned")
    df_campaigns_information = display_databases(directory_path, file_name = "campaigns_information", datetime_col = ['opened_at', 'sent_at', 'campaign_sent_at'])
    df_products_purchased_reduced = display_databases(directory_path, file_name = "products_purchased_reduced", datetime_col = ['purchase_date'])
    
    # Filtre de cohérence pour la mise en pratique de notre méthode
    max_date =  pd.to_datetime(max_date, utc = True, format = 'ISO8601') 
    end_features_date = pd.to_datetime(end_features_date, utc = True, format = 'ISO8601')
    min_date = pd.to_datetime(min_date, utc = True, format = 'ISO8601')

    #Filtre de la base df_campaigns_information
    df_campaigns_information = df_campaigns_information[(df_campaigns_information['sent_at'] <= end_features_date) & (df_campaigns_information['sent_at'] >= min_date)]
    df_campaigns_information['opened_at'][df_campaigns_information['opened_at'] >= end_features_date] = np.datetime64('NaT')
    
    #Filtre de la base df_products_purchased_reduced
    df_products_purchased_reduced = df_products_purchased_reduced[(df_products_purchased_reduced['purchase_date'] <= end_features_date) & (df_products_purchased_reduced['purchase_date'] >= min_date)]

    print("Data filtering : SUCCESS")
    
    # Fusion de l'ensemble et creation des KPI

    # KPI sur les campagnes publicitaires
    df_campaigns_kpi = campaigns_kpi_function(campaigns_information = df_campaigns_information) 

    # KPI sur le comportement d'achat
    df_tickets_kpi = tickets_kpi_function(tickets_information = df_products_purchased_reduced)

    # KPI sur les données socio-démographiques
    df_customerplus_clean = customerplus_kpi_function(customerplus_clean = df_customerplus_clean_0)
    
    print("KPIs construction : SUCCESS")
    
    # Fusion avec KPI liés au customer
    df_customer = pd.merge(df_customerplus_clean, df_campaigns_kpi, on = 'customer_id', how = 'left')
    
    # Fill NaN values
    df_customer[['nb_campaigns', 'nb_campaigns_opened']] = df_customer[['nb_campaigns', 'nb_campaigns_opened']].fillna(0)
    
    # Fusion avec KPI liés au comportement d'achat
    df_customer_product = pd.merge(df_tickets_kpi, df_customer, on = 'customer_id', how = 'outer')
    
    # Fill NaN values
    df_customer_product[['nb_tickets', 'nb_purchases', 'total_amount', 'nb_suppliers', 'vente_internet_max', 'nb_tickets_internet']] = df_customer_product[['nb_tickets', 'nb_purchases', 'total_amount', 'nb_suppliers', 'vente_internet_max', 'nb_tickets_internet']].fillna(0)

    print("Explanatory variable construction : SUCCESS")

    # 2. Construction of the explained variable 
    df_products_purchased_to_predict = df_products_purchased_reduced[(df_products_purchased_reduced['purchase_date'] <= max_date) & (df_products_purchased_reduced['purchase_date'] > end_features_date)]

    # Indicatrice d'achat
    df_products_purchased_to_predict['y_has_purchased'] = 1

    y = df_products_purchased_to_predict[['customer_id', 'y_has_purchased']].drop_duplicates()

    print("Explained variable construction : SUCCESS")
    
    # 3. Merge between explained and explanatory variables
    dataset = pd.merge(df_customer_product, y, on = ['customer_id'], how = 'left')

    # 0 if there is no purchase
    dataset[['y_has_purchased']].fillna(0)    
    
    return dataset

In [99]:
# Create test dataset and train dataset for sport companies

start_date, end_of_features, final_date = df_coverage_modelization(list_of_comp, coverage_train = 0.7)

for company in list_of_comp:
    dataset_test = dataset_construction(min_date = start_date, end_features_date = end_of_features,
                                        max_date = final_date, directory_path = company) 

File path :  projet-bdc2324-team1/0_Input/Company_10/products_purchased_reduced.csv


<string>:13: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.


Couverture Company 10 : 2016-03-07 - 2023-09-25
File path :  projet-bdc2324-team1/0_Input/Company_11/products_purchased_reduced.csv


<string>:13: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.


Couverture Company 11 : 2015-06-26 - 2023-11-08
File path :  projet-bdc2324-team1/0_Input/Company_12/products_purchased_reduced.csv


...

File path :  projet-bdc2324-team1/0_Input/Company_14/products_purchased_reduced.csv


<string>:13: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
<string>:13: DtypeWarning: Columns (8,9) have mixed types. Specify dtype option on import or set low_memory=False.
/tmp/ipykernel_438/573049956.py:55: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps upd

Data filtering : SUCCESS


<string>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


KPIs construction : SUCCESS
Explanatory variable construction : SUCCESS
Explained variable construction : SUCCESS


In [103]:
  # Exportation
FILE_KEY_OUT_S3 = "dataset_test" + company +  ".csv"
FILE_PATH_OUT_S3 = BUCKET_OUT + "/" + FILE_KEY_OUT_S3
    
with fs.open(FILE_PATH_OUT_S3, 'w') as file_out:
    dataset_test.to_csv(file_out, index = False)
    
print("Exportation dataset test : SUCCESS")

Exportation dataset test : SUCCESS


In [104]:
FILE_PATH_OUT_S3

'projet-bdc2324-team1/Generalization/musique/dataset_test14.csv'

In [105]:
dataset_test14

NameError: name 'dataset_test14' is not defined